In [1]:
import pandas as pd
import numpy as np
import os
import json
import theguardian_content


In [2]:
window_size = 6
datapath = "windowed_diff_data"
pos = ['GK_', 'DEF_', 'FWD_', 'MID_']
dfs = [pd.read_csv("{}/{}_{}.csv".format(datapath, p, window_size)) for p in pos]
players_by_pos = {}
for i in range(len(pos)):
    players_by_pos[pos[i]] = list(dfs[i]['name'].unique())
save_path = "./player_news_json/"


In [20]:
player_article = {}
iteration = 0
for player in players_by_pos['GK_']:
    print(iteration)
    results = []
    headers = {"q": player, "from-date": "2021-08-01", "to-date": "2022-06-01", "use-date": "last-modified", "page-size": "50", "order-date": "last-modified", "show-fields": "bodyText"}
    content = theguardian_content.Content(api='6ce34e7f-339f-42d4-b33b-f2377197523a', **headers)
    json_content = content.get_content_response()
    all_results = content.get_results(json_content)
    new_results = []
    for b in all_results: 
        new_dict = {}
        new_dict["webPublicationDate"] = b["webPublicationDate"]
        cutoff = 512
        if(len(b["fields"]['bodyText'])>cutoff):
            cutoff = len(b["fields"]['bodyText'])
        new_dict["text"] = b["fields"]['bodyText'][:cutoff]
        new_results.append(new_dict)
    results += all_results
    pages = int(json_content['response']['pages'])
    for i in range(2, pages+1):
        headers = {"q": player, "from-date": "2021-08-01", "to-date": "2022-06-01", "use-date": "last-modified", "page-size": "50", "order-date": "last-modified", "page": str(i),  "show-fields": "bodyText"}
        content = theguardian_content.Content(api='6ce34e7f-339f-42d4-b33b-f2377197523a', **headers)
        json_content = content.get_content_response()
        all_results = content.get_results(json_content)
        new_results = []
        for b in all_results: 
            new_dict = {}
            new_dict["webPublicationDate"] = b["webPublicationDate"]
            cutoff = 512
            if(len(b["fields"]['bodyText'])>cutoff):
                cutoff = len(b["fields"]['bodyText'])
            new_dict["text"] = b["fields"]['bodyText'][:cutoff]
            new_results.append(new_dict)
        results += all_results
        print("page: " + str(i))
    player_article[player] = results
    iteration += 1
with open(save_path + 'GK_news.csv', 'w') as fp:
    json.dump(player_article, fp)


0
page: 2
1
page: 2
page: 3
page: 4
page: 5
page: 6
page: 7
page: 8
page: 9
page: 10
page: 11
page: 12
page: 13
page: 14
page: 15
page: 16
page: 17
page: 18
page: 19
page: 20
page: 21
2
page: 2
page: 3
page: 4
page: 5
page: 6
page: 7
page: 8
page: 9
page: 10
page: 11
page: 12
page: 13
page: 14
page: 15
page: 16
page: 17
page: 18
page: 19
page: 20
page: 21
page: 22
page: 23
page: 24
page: 25
page: 26
page: 27
page: 28
page: 29
3
page: 2
page: 3
page: 4
page: 5
page: 6
page: 7
page: 8
page: 9
page: 10
page: 11
page: 12
page: 13
page: 14
page: 15
page: 16
page: 17
page: 18
page: 19
page: 20
page: 21
page: 22
page: 23
page: 24
page: 25
page: 26
page: 27
page: 28
page: 29
page: 30
page: 31
page: 32
page: 33
page: 34
page: 35
page: 36
page: 37
page: 38
page: 39
page: 40
page: 41
page: 42
page: 43
page: 44
page: 45
page: 46
page: 47
page: 48
page: 49
page: 50
page: 51
4
page: 2
page: 3
page: 4
page: 5
page: 6
page: 7
page: 8
page: 9
page: 10
page: 11
page: 12
page: 13
page: 14
page: 15
page: 

In [37]:
player_article_gk = json.load(open(save_path + 'GK_news.json', 'r'))
df_gk = dfs[0]
window_cutoff = 3
columns_csv = ['assists', 'clean_sheets', 'creativity', 'bps',
               'goals_conceded', 'goals_scored', 'ict_index', 'influence',
               'minutes', 'own_goals', 'penalties_missed',
               'penalties_saved', 'red_cards', 'saves',
               'threat', 'yellow_cards', 
               'total_points']
columns_not_roll = ['was_home', 'difficulty_gap']
temp_df = pd.DataFrame(columns=['input', 'output'])
temp_df["output"] = df_gk['total_points_bin']
from datetime import datetime
import string
printable = set(string.printable)
all_inputs = []
for index, row in df_gk.iterrows():
    get_kick_off_time = row['kickoff_time'][:row['kickoff_time'].index("T")]
    kick_off_date = datetime.strptime(get_kick_off_time, "%Y-%m-%d")
    player_name = row['name']
    total_str = "The rolling averages over the last " + str(window_size) + " weeks\n"
    articles_to_parse = []
    for i in range(2, len(player_article_gk[row['name']])):
        curr_article_time = player_article_gk[row['name']][i]["webPublicationDate"]
        curr_article_time = curr_article_time[:curr_article_time.index("T")]
        curr_article_time = datetime.strptime(curr_article_time, "%Y-%m-%d")
        if kick_off_date >= curr_article_time:
            cutoff = window_cutoff
            if i + cutoff > len(player_article_gk[row['name']]):
                cutoff = len(player_article_gk[row['name']]) - i
            articles_to_parse = player_article_gk[row['name']][i: cutoff]
            break
    for col in columns_csv:
        total_str += "{}: {} ".format(col, str(round(row[col], 3)))
    total_str += "For this game, these are the stats\n"
    for col in columns_not_roll:
        total_str += "{}: {} ".format(col, str(round(row[col], 3)))
    total_str += "\n"
    for article in articles_to_parse: 
        cutoff = 512
        bodyText = article["fields"]['bodyText']
        bodyText = ''.join(filter(lambda x: x in printable, bodyText))
        if(len(bodyText)>cutoff):
            cutoff = len(bodyText)
        total_str += bodyText[:cutoff] + "\n"
    all_inputs.append(total_str)
print(all_inputs)
temp_df['input'] = all_inputs
temp_df.to_csv("TL_data/GK_"+str(window_size)+".csv", index=False)


['The rolling averages over the last 6 weeks\nassists: 0.0 clean_sheets: 0.167 creativity: 0.0 bps: 18.5 goals_conceded: 1.667 goals_scored: 0.0 ict_index: 2.733 influence: 27.167 minutes: 90.0 own_goals: 0.0 penalties_missed: 0.0 penalties_saved: 0.0 red_cards: 0.0 saves: 3.5 threat: 0.0 yellow_cards: 0.0 total_points: 3.333 For this game, these are the stats\nwas_home: 0 difficulty_gap: 0 \n', 'The rolling averages over the last 6 weeks\nassists: 0.0 clean_sheets: 0.143 creativity: 0.0 bps: 17.571 goals_conceded: 1.714 goals_scored: 0.0 ict_index: 2.629 influence: 26.114 minutes: 90.0 own_goals: 0.0 penalties_missed: 0.0 penalties_saved: 0.0 red_cards: 0.0 saves: 3.286 threat: 0.0 yellow_cards: 0.0 total_points: 3.0 For this game, these are the stats\nwas_home: 1 difficulty_gap: 0 \n', 'The rolling averages over the last 6 weeks\nassists: 0.0 clean_sheets: 0.0 creativity: 0.0 bps: 16.0 goals_conceded: 2.0 goals_scored: 0.0 ict_index: 2.643 influence: 26.229 minutes: 90.0 own_goals: 0

In [39]:
player_article = {}
iteration = 0
print(len(players_by_pos['FWD_']))
for player in players_by_pos['FWD_']:
    print(iteration)
    results = []
    headers = {"q": player, "from-date": "2021-08-01", "to-date": "2022-06-01", "use-date": "last-modified", "page-size": "50", "order-date": "last-modified", "show-fields": "bodyText"}
    content = theguardian_content.Content(api='cf806909-5e3f-486f-ae62-8759ae746915', **headers)
    try:
        json_content = content.get_content_response()
        all_results = content.get_results(json_content)
    except:
        break
    new_results = []
    for b in all_results: 
        new_dict = {}
        new_dict["webPublicationDate"] = b["webPublicationDate"]
        cutoff = 512
        if(len(b["fields"]['bodyText'])>cutoff):
            cutoff = len(b["fields"]['bodyText'])
        new_dict["text"] = b["fields"]['bodyText'][:cutoff]
        new_results.append(new_dict)
    results += all_results
    pages = int(json_content['response']['pages'])
    for i in range(2, pages+1):
        headers = {"q": player, "from-date": "2021-08-01", "to-date": "2022-06-01", "use-date": "last-modified", "page-size": "50", "order-date": "last-modified", "page": str(i),  "show-fields": "bodyText"}
        content = theguardian_content.Content(api='cf806909-5e3f-486f-ae62-8759ae746915', **headers)
        try:
            json_content = content.get_content_response()
            all_results = content.get_results(json_content)
        except:
            break
        new_results = []
        for b in all_results: 
            new_dict = {}
            new_dict["webPublicationDate"] = b["webPublicationDate"]
            cutoff = 512
            if(len(b["fields"]['bodyText'])>cutoff):
                cutoff = len(b["fields"]['bodyText'])
            new_dict["text"] = b["fields"]['bodyText'][:cutoff]
            new_results.append(new_dict)
        results += all_results
        print("page: " + str(i))
    player_article[player] = results
    iteration += 1
with open(save_path + 'FWD_news.csv', 'w') as fp:
    json.dump(player_article, fp)


67
0
page: 2
page: 3
page: 4
page: 5
page: 6
page: 7
page: 8
page: 9
page: 10
1
page: 2
page: 3
page: 4
page: 5
page: 6
page: 7
page: 8
page: 9
page: 10
page: 11
page: 12
page: 13
page: 14
page: 15
page: 16
page: 17
page: 18
page: 19
page: 20
page: 21
page: 22
page: 23
page: 24
page: 25
page: 26
page: 27
page: 28
page: 29
page: 30
page: 31
page: 32
2
page: 2
page: 3
page: 4
page: 5
page: 6
page: 7
page: 8
page: 9
page: 10
page: 11
page: 12
page: 13
page: 14
page: 15
page: 16
3
page: 2
page: 3
page: 4
page: 5
page: 6
page: 7
page: 8
page: 9
page: 10
page: 11
page: 12
page: 13
page: 14
page: 15
page: 16
page: 17
page: 18
page: 19
page: 20
page: 21
page: 22
page: 23
page: 24
page: 25
4
page: 2
page: 3
page: 4
page: 5
page: 6
page: 7
page: 8
page: 9
page: 10
page: 11
page: 12
page: 13
page: 14
page: 15
page: 16
page: 17
page: 18
page: 19
page: 20
page: 21
page: 22
page: 23
page: 24
page: 25
page: 26
page: 27
page: 28
page: 29
page: 30
5
page: 2
page: 3
page: 4
page: 5
page: 6
page: 7
page:

KeyError: 'response'

In [54]:
player_article_fwd = json.load(open(save_path + 'FWD_news.json', 'r'))
df_fwd = dfs[2]
window_cutoff = 3
columns_csv = ['assists', 'clean_sheets', 'creativity', 'bps',
               'goals_conceded', 'goals_scored', 'ict_index', 'influence',
               'minutes', 'own_goals', 'penalties_missed',
               'penalties_saved', 'red_cards', 'saves',
               'threat', 'yellow_cards', 
               'total_points']
columns_not_roll = ['was_home', 'difficulty_gap']
temp_df = pd.DataFrame(columns=['input', 'output'])
temp_df["output"] = df_fwd['total_points_bin']
from datetime import datetime
import string
printable = set(string.printable)
all_inputs = []
for index, row in df_fwd.iterrows():
    get_kick_off_time = row['kickoff_time'][:row['kickoff_time'].index("T")]
    kick_off_date = datetime.strptime(get_kick_off_time, "%Y-%m-%d")
    player_name = row['name']
    total_str = "The rolling averages over the last " + str(window_size) + " weeks\n"
    articles_to_parse = []
    if row['name'] in player_article_fwd:
        for i in range(2, len(player_article_fwd[row['name']])):
            curr_article_time = player_article_fwd[row['name']][i]["webPublicationDate"]
            curr_article_time = curr_article_time[:curr_article_time.index("T")]
            curr_article_time = datetime.strptime(curr_article_time, "%Y-%m-%d")
            if kick_off_date >= curr_article_time:
                cutoff = window_cutoff
                if i + cutoff > len(player_article_fwd[row['name']]):
                    cutoff = len(player_article_fwd[row['name']]) - i
                articles_to_parse = player_article_fwd[row['name']][i: cutoff]
                break
    for col in columns_csv:
        total_str += "{}: {} ".format(col, str(round(row[col], 3)))
    total_str += "For this game, these are the stats\n"
    for col in columns_not_roll:
        total_str += "{}: {} ".format(col, str(round(row[col], 3)))
    total_str += "\n"
    for article in articles_to_parse: 
        cutoff = 512
        bodyText = article["fields"]['bodyText']
        bodyText = ''.join(filter(lambda x: x in printable, bodyText))
        if(len(bodyText)>cutoff):
            cutoff = len(bodyText)
        total_str += bodyText[:cutoff] + "\n"
    all_inputs.append(total_str)
print(all_inputs)
temp_df['input'] = all_inputs
temp_df.to_csv("TL_data/FWD_"+str(window_size)+".csv", index=False)


['The rolling averages over the last 6 weeks\nassists: 0.0 clean_sheets: 0.0 creativity: 5.267 bps: 6.5 goals_conceded: 0.333 goals_scored: 0.167 ict_index: 2.0 influence: 8.0 minutes: 17.0 own_goals: 0.0 penalties_missed: 0.0 penalties_saved: 0.0 red_cards: 0.0 saves: 0.0 threat: 6.667 yellow_cards: 0.0 total_points: 1.667 For this game, these are the stats\nwas_home: 1 difficulty_gap: 0 \n', 'The rolling averages over the last 6 weeks\nassists: 0.0 clean_sheets: 0.0 creativity: 4.557 bps: 6.0 goals_conceded: 0.571 goals_scored: 0.143 ict_index: 1.771 influence: 7.143 minutes: 17.714 own_goals: 0.0 penalties_missed: 0.0 penalties_saved: 0.0 red_cards: 0.0 saves: 0.0 threat: 6.0 yellow_cards: 0.0 total_points: 1.571 For this game, these are the stats\nwas_home: 0 difficulty_gap: -2 \n', 'The rolling averages over the last 6 weeks\nassists: 0.143 clean_sheets: 0.143 creativity: 8.329 bps: 15.857 goals_conceded: 0.571 goals_scored: 0.429 ict_index: 4.686 influence: 19.686 minutes: 26.429

In [52]:
player_article = {}
api_key_list = ['dbb21fef-bb93-4680-80fb-55ee28fb7cc2', '48867736-37c4-43d8-b95e-cfda12765be2', '5784d366-6358-453b-8d66-0137d991e356','d16f6356-cd2f-4f72-87c0-5abec2ae0131', 'c462cfb2-29fb-435b-bc48-1c5573262a41', '4fc7fa88-5820-4b47-9b92-95b85b114f7a','50ff0b48-7d30-4725-9346-a0be359140e0', 'b9b26e89-e2b4-42c5-b1c1-387eb6a1032d']
api_index = 0
iteration = 0
print(len(players_by_pos['MID_']))
for player in players_by_pos['MID_']:
    print(iteration)
    results = []
    headers = {"q": player, "from-date": "2021-08-01", "to-date": "2022-06-01", "use-date": "last-modified", "page-size": "50", "order-date": "last-modified", "show-fields": "bodyText"}
    all_results = []
    try:
        content = theguardian_content.Content(api=api_key_list[api_index], **headers)
        json_content = content.get_content_response()
        all_results = content.get_results(json_content)
    except:
        api_index+=1
        while api_index >= len(api_key_list):
            try:
                content = theguardian_content.Content(api=api_key_list[api_index], **headers)
                json_content = content.get_content_response()
                all_results = content.get_results(json_content)
            except:
                api_index+=1
        if api_index >= len(api_key_list):
            break
    new_results = []
    for b in all_results: 
        new_dict = {}
        new_dict["webPublicationDate"] = b["webPublicationDate"]
        cutoff = 512
        if(len(b["fields"]['bodyText'])>cutoff):
            cutoff = len(b["fields"]['bodyText'])
        new_dict["text"] = b["fields"]['bodyText'][:cutoff]
        new_results.append(new_dict)
    results += new_results
    pages = int(json_content['response']['pages'])
    for i in range(2, pages+1):
        headers = {"q": player, "from-date": "2021-08-01", "to-date": "2022-06-01", "use-date": "last-modified", "page-size": "50", "order-date": "last-modified", "page": str(i),  "show-fields": "bodyText"}
        content = theguardian_content.Content(api='cf806909-5e3f-486f-ae62-8759ae746915', **headers)
        all_results = []
        try:
            content = theguardian_content.Content(api=api_key_list[api_index], **headers)
            json_content = content.get_content_response()
            all_results = content.get_results(json_content)
        except:
            api_index+=1
            while api_index >= len(api_key_list):
                try:
                    content = theguardian_content.Content(api=api_key_list[api_index], **headers)
                    json_content = content.get_content_response()
                    all_results = content.get_results(json_content)
                except:
                    api_index+=1
            if api_index >= len(api_key_list):
                break
        new_results = []
        for b in all_results: 
            new_dict = {}
            new_dict["webPublicationDate"] = b["webPublicationDate"]
            cutoff = 512
            if(len(b["fields"]['bodyText'])>cutoff):
                cutoff = len(b["fields"]['bodyText'])
            new_dict["text"] = b["fields"]['bodyText'][:cutoff]
            new_results.append(new_dict)
        results += new_results
        print("page: " + str(i))
    player_article[player] = results
    iteration += 1
with open(save_path + 'MID_news.json', 'w') as fp:
    json.dump(player_article, fp)


227
0
page: 2
page: 3
page: 4
page: 5
page: 6
page: 7
page: 8
page: 9
page: 10
page: 11
page: 12
page: 13
page: 14
1
page: 2
page: 3
page: 4
page: 5
page: 6
page: 7
page: 8
page: 9
page: 10
page: 11
page: 12
page: 13
page: 14
page: 15
page: 16
page: 17
page: 18
page: 19
page: 20
page: 21
page: 22
page: 23
page: 24
page: 25
page: 26
page: 27
page: 28
page: 29
page: 30
page: 31
page: 32
2
page: 2
page: 3
page: 4
page: 5
page: 6
page: 7
page: 8
page: 9
page: 10
page: 11
page: 12
page: 13
page: 14
page: 15
page: 16
3
page: 2
4
page: 2
page: 3
page: 4
page: 5
page: 6
page: 7
page: 8
page: 9
page: 10
page: 11
page: 12
page: 13
5
page: 2
page: 3
page: 4
page: 5
page: 6
page: 7
6
page: 2
page: 3
page: 4
page: 5
page: 6
page: 7
page: 8
page: 9
page: 10
7
page: 2
page: 3
page: 4
page: 5
page: 6
page: 7
page: 8
page: 9
page: 10
page: 11
page: 12
page: 13
page: 14
page: 15
page: 16
page: 17
page: 18
page: 19
8
page: 2
9
page: 2
page: 3
10
page: 2
page: 3
page: 4
page: 5
page: 6
page: 7
page: 8
pag

In [16]:
import ast
text = ""
with open(save_path + 'MID_news.json', 'r') as f:
    while True:
        chunk = f.read(1000)
        if chunk == '':
            break
        text += chunk
player_article_mid = ast.literal_eval(text)
df_mid = dfs[3]
window_cutoff = 3
columns_csv = ['assists', 'clean_sheets', 'creativity', 'bps',
               'goals_conceded', 'goals_scored', 'ict_index', 'influence',
               'minutes', 'own_goals', 'penalties_missed',
               'penalties_saved', 'red_cards', 'saves',
               'threat', 'yellow_cards', 
               'total_points']
columns_not_roll = ['was_home', 'difficulty_gap']
temp_df = pd.DataFrame(columns=['input', 'output'])
temp_df["output"] = df_mid['total_points_bin']
from datetime import datetime
import string
printable = set(string.printable)
all_inputs = []
i = 0
for index, row in df_mid.iterrows():
    get_kick_off_time = row['kickoff_time'][:row['kickoff_time'].index("T")]
    kick_off_date = datetime.strptime(get_kick_off_time, "%Y-%m-%d")
    player_name = row['name']
    total_str = "The rolling averages over the last " + str(window_size) + " weeks\n"
    articles_to_parse = []
    if row['name'] in player_article_mid:
        for i in range(2, len(player_article_mid[row['name']])):
            curr_article_time = player_article_mid[row['name']][i]["webPublicationDate"]
            curr_article_time = curr_article_time[:curr_article_time.index("T")]
            curr_article_time = datetime.strptime(curr_article_time, "%Y-%m-%d")
            if kick_off_date >= curr_article_time:
                cutoff = window_cutoff
                if i + cutoff > len(player_article_mid[row['name']]):
                    cutoff = len(player_article_mid[row['name']]) - i
                articles_to_parse = player_article_mid[row['name']][i: cutoff]
                break
    for col in columns_csv:
        total_str += "{}: {} ".format(col, str(round(row[col], 3)))
    total_str += "For this game, these are the stats\n"
    for col in columns_not_roll:
        total_str += "{}: {} ".format(col, str(round(row[col], 3)))
    total_str += "\n"
    for article in articles_to_parse: 
        bodyText = article['text']
        bodyText = ''.join(filter(lambda x: x in printable, bodyText))
        total_str += bodyText + "\n"
    all_inputs.append(total_str)
print(i)
temp_df['input'] = all_inputs
temp_df.to_csv("TL_data/MID_"+str(window_size)+".csv", index=False)
player_article_mid = {}


3


In [17]:
player_article = {}
api_key_list = ['dbb21fef-bb93-4680-80fb-55ee28fb7cc2', '48867736-37c4-43d8-b95e-cfda12765be2', '5784d366-6358-453b-8d66-0137d991e356','d16f6356-cd2f-4f72-87c0-5abec2ae0131', 'c462cfb2-29fb-435b-bc48-1c5573262a41', '4fc7fa88-5820-4b47-9b92-95b85b114f7a','50ff0b48-7d30-4725-9346-a0be359140e0', 'b9b26e89-e2b4-42c5-b1c1-387eb6a1032d', '9a475009-f5c4-472c-b22e-7ec79c682230', '3bf5819-ced8-464f-8b38-addd0422ea2f', 'a231628e-398b-45b2-9b79-6557f2d3355e', ' b1d0d99b-27b2-45f8-ab10-4511d84a192a', 'b6a0507f-b5dc-4ec5-93ff-aefb515f05b3']
api_index = 0
iteration = 0
print(len(players_by_pos['DEF_']))
for player in players_by_pos['DEF_']:
    print(iteration)
    results = []
    headers = {"q": player, "from-date": "2021-08-01", "to-date": "2022-06-01", "use-date": "last-modified", "page-size": "50", "order-date": "last-modified", "show-fields": "bodyText"}
    all_results = []
    try:
        content = theguardian_content.Content(api=api_key_list[api_index], **headers)
        json_content = content.get_content_response()
        all_results = content.get_results(json_content)
    except:
        api_index+=1
        while api_index >= len(api_key_list):
            try:
                content = theguardian_content.Content(api=api_key_list[api_index], **headers)
                json_content = content.get_content_response()
                all_results = content.get_results(json_content)
            except:
                api_index+=1
        if api_index >= len(api_key_list):
            break
    new_results = []
    for b in all_results: 
        new_dict = {}
        new_dict["webPublicationDate"] = b["webPublicationDate"]
        cutoff = 512
        if(len(b["fields"]['bodyText'])>cutoff):
            cutoff = len(b["fields"]['bodyText'])
        new_dict["text"] = b["fields"]['bodyText'][:cutoff]
        new_results.append(new_dict)
    results += new_results
    pages = int(json_content['response']['pages'])
    for i in range(2, pages+1):
        headers = {"q": player, "from-date": "2021-08-01", "to-date": "2022-06-01", "use-date": "last-modified", "page-size": "50", "order-date": "last-modified", "page": str(i),  "show-fields": "bodyText"}
        content = theguardian_content.Content(api='cf806909-5e3f-486f-ae62-8759ae746915', **headers)
        all_results = []
        try:
            content = theguardian_content.Content(api=api_key_list[api_index], **headers)
            json_content = content.get_content_response()
            all_results = content.get_results(json_content)
        except:
            api_index+=1
            while api_index >= len(api_key_list):
                try:
                    content = theguardian_content.Content(api=api_key_list[api_index], **headers)
                    json_content = content.get_content_response()
                    all_results = content.get_results(json_content)
                except:
                    api_index+=1
            if api_index >= len(api_key_list):
                break
        new_results = []
        for b in all_results: 
            new_dict = {}
            new_dict["webPublicationDate"] = b["webPublicationDate"]
            cutoff = 512
            if(len(b["fields"]['bodyText'])>cutoff):
                cutoff = len(b["fields"]['bodyText'])
            new_dict["text"] = b["fields"]['bodyText'][:cutoff]
            new_results.append(new_dict)
        results += new_results
        print("page: " + str(i))
    player_article[player] = results
    iteration += 1
with open(save_path + 'DEF_news.json', 'w') as fp:
    json.dump(player_article, fp)


181
0
page: 2
page: 3
1
page: 2
page: 3
page: 4
page: 5
page: 6
page: 7
page: 8
page: 9
page: 10
page: 11
page: 12
page: 13
page: 14
page: 15
page: 16
page: 17
page: 18
page: 19
2
page: 2
page: 3
page: 4
page: 5
page: 6
page: 7
page: 8
page: 9
page: 10
page: 11
page: 12
page: 13
page: 14
page: 15
page: 16
page: 17
page: 18
page: 19
page: 20
page: 21
page: 22
page: 23
page: 24
page: 25
page: 26
page: 27
3
page: 2
page: 3
page: 4
page: 5
page: 6
page: 7
page: 8
page: 9
page: 10
page: 11
page: 12
page: 13
page: 14
page: 15
page: 16
page: 17
page: 18
page: 19
page: 20
page: 21
page: 22
page: 23
page: 24
page: 25
page: 26
page: 27
page: 28
page: 29
page: 30
page: 31
page: 32
page: 33
page: 34
page: 35
page: 36
4
page: 2
page: 3
page: 4
page: 5
page: 6
page: 7
page: 8
page: 9
page: 10
page: 11
page: 12
page: 13
page: 14
page: 15
page: 16
page: 17
page: 18
page: 19
page: 20
page: 21
5
page: 2
page: 3
page: 4
page: 5
page: 6
page: 7
page: 8
page: 9
page: 10
6
page: 2
page: 3
page: 4
page: 5
pa

In [18]:
text = ""
with open(save_path + 'DEF_news.json', 'r') as f:
    while True:
        chunk = f.read(1000)
        if chunk == '':
            break
        text += chunk
player_article_def = ast.literal_eval(text)
df_def = dfs[1]
window_cutoff = 3
columns_csv = ['assists', 'clean_sheets', 'creativity', 'bps',
               'goals_conceded', 'goals_scored', 'ict_index', 'influence',
               'minutes', 'own_goals', 'penalties_missed',
               'penalties_saved', 'red_cards', 'saves',
               'threat', 'yellow_cards', 
               'total_points']
columns_not_roll = ['was_home', 'difficulty_gap']
temp_df = pd.DataFrame(columns=['input', 'output'])
temp_df["output"] = df_mid['total_points_bin']
from datetime import datetime
import string
printable = set(string.printable)
all_inputs = []
i = 0
for index, row in df_def.iterrows():
    get_kick_off_time = row['kickoff_time'][:row['kickoff_time'].index("T")]
    kick_off_date = datetime.strptime(get_kick_off_time, "%Y-%m-%d")
    player_name = row['name']
    total_str = "The rolling averages over the last " + str(window_size) + " weeks\n"
    articles_to_parse = []
    if row['name'] in player_article_def:
        for i in range(2, len(player_article_def[row['name']])):
            curr_article_time = player_article_def[row['name']][i]["webPublicationDate"]
            curr_article_time = curr_article_time[:curr_article_time.index("T")]
            curr_article_time = datetime.strptime(curr_article_time, "%Y-%m-%d")
            if kick_off_date >= curr_article_time:
                cutoff = window_cutoff
                if i + cutoff > len(player_article_def[row['name']]):
                    cutoff = len(player_article_def[row['name']]) - i
                articles_to_parse = player_article_def[row['name']][i: cutoff]
                break
    for col in columns_csv:
        total_str += "{}: {} ".format(col, str(round(row[col], 3)))
    total_str += "For this game, these are the stats\n"
    for col in columns_not_roll:
        total_str += "{}: {} ".format(col, str(round(row[col], 3)))
    total_str += "\n"
    for article in articles_to_parse: 
        bodyText = article['text']
        bodyText = ''.join(filter(lambda x: x in printable, bodyText))
        total_str += bodyText + "\n"
    all_inputs.append(total_str)
print(i)
temp_df['input'] = all_inputs
temp_df.to_csv("TL_data/MID_"+str(window_size)+".csv", index=False)
player_article_def = {}


KeyError: 'Nathaniel Clyne'